## Optuna

Будем тестить как работает optuna на [датасете](https://yadi.sk/d/BNR41Vu3y0c7qA). В нём 200 классов и около 5 тысяч картинок на каждый класс. Классы пронумерованы, как нетрудно догадаться, от 0 до 199. 

In [4]:
import torch
import optuna
import torchvision 
import matplotlib.pyplot as plt

import torch.optim as optim
from torch import nn
from tqdm import tqdm, trange
from torch.utils.data import DataLoader
from torchmetrics.functional import accuracy
from torchvision import transforms
from torchvision.datasets import ImageFolder
from optuna.trial import TrialState

In [5]:
transform = transforms.Compose(
    [transforms.ColorJitter(hue=.05, saturation=.05),
        transforms.RandomHorizontalFlip(),
        transforms.RandomInvert(p = 0.15),
        transforms.RandomRotation(30),
        torchvision.transforms.ToTensor(),
     torchvision.transforms.Normalize((0.5, 0.5, 0.5), (0.5, 0.5, 0.5))])

train_dataset = ImageFolder('./dataset/dataset/train', transform=transform)
val_dataset = ImageFolder('./dataset/dataset/val', transform=transform)


train_dataloader = DataLoader(train_dataset, 
    batch_size=64,
    shuffle=True) # YOUR CODE HERE
val_dataloader = DataLoader(val_dataset, 
    batch_size=64,
    shuffle=False)

In [9]:
f = next(iter(train_dataloader))

In [ ]:
f

In [ ]:
plt.imshow(f[0][8].permute(1, 2, 0))

In [6]:
class YourNet(torch.nn.Module):
    def __init__(self,dropout=0.4, extend = 2, channel =8,extend_lin=2,act ="ELU"):
        super().__init__()
        # -------------------------------------------
        # Архитектура сетки
        # -------------------------------------------
        if act =="ReLU":
            self.act = torch.nn.ReLU()
        elif act == "LeakyReLU": 
             self.act =nn.LeakyReLU(negative_slope=0.01)
        else: 
            self.act = nn.ELU()
        self.batch_norm1 = torch.nn.BatchNorm2d(3)
        #self.batch_norm3 = torch.nn.BatchNorm1d(512)
        #self.batch_norm4 = torch.nn.BatchNorm1d(1024)
        self.maxpool = torch.nn.MaxPool2d(kernel_size=3, stride=2, padding=1)
        
        self.conv0 = torch.nn.Sequential(nn.Conv2d(in_channels=3, out_channels=channel, kernel_size=3, stride=1, padding=1),
        nn.BatchNorm2d(channel),
        self.act)
        
        self.conv1 = torch.nn.Sequential( 
            torch.nn.Conv2d(in_channels=channel, out_channels=channel, kernel_size=3,padding = 1),
            torch.nn.BatchNorm2d(channel),
            self.act,
            torch.nn.Conv2d(in_channels=channel, out_channels=channel, kernel_size=3,padding = 1),
            torch.nn.Dropout(p=dropout),
            torch.nn.BatchNorm2d(channel))
        self.conv2_0 = torch.nn.Conv2d(in_channels=channel, out_channels=channel*extend, kernel_size=3,stride = 2,padding=1)
        self.concat1 = nn.Conv2d(in_channels=channel, out_channels=channel*extend, kernel_size=1, stride=2)
        channel = channel*extend
        self.conv2_1 = torch.nn.Conv2d(in_channels=channel, out_channels=channel, kernel_size=3,padding=1)
        self.conv2 = torch.nn.Sequential(
            torch.nn.BatchNorm2d(channel),
            self.act,
            torch.nn.Conv2d(in_channels=channel, out_channels=channel, kernel_size=3,padding=1),
            torch.nn.Dropout(p=dropout),
            torch.nn.BatchNorm2d(channel)
        )
#         self.conv3_0 = torch.nn.Conv2d(in_channels=channel, out_channels=channel*extend, kernel_size=3,stride = 2,padding=1)
#         self.concat2 = nn.Conv2d(in_channels=channel, out_channels=channel*extend, kernel_size=1, stride=2)
#         channel=channel*extend
#         self.conv3_1 = torch.nn.Conv2d(in_channels=channel, out_channels=channel, kernel_size=3,padding=1)
#         self.conv3 = torch.nn.Sequential(
#             torch.nn.BatchNorm2d(channel),
#             self.act,
#             torch.nn.Conv2d(in_channels=channel, out_channels=channel, kernel_size=3,padding=1),
#             torch.nn.Dropout(p=dropout),
#             torch.nn.BatchNorm2d(channel)
#         )
#         self.conv4_0 = torch.nn.Conv2d(in_channels=channel, out_channels=channel*extend, kernel_size=3,stride = 2,padding=1)
#         self.concat3 = nn.Conv2d(in_channels=channel, out_channels=channel*extend, kernel_size=1, stride=2)
#         channel= channel*extend
        
#         self.conv4_1 = torch.nn.Conv2d(in_channels=channel, out_channels=channel, kernel_size=3,padding=1,groups=8)
#         self.conv4 = torch.nn.Sequential(
#             torch.nn.BatchNorm2d(channel),
#             self.act,
#             torch.nn.Conv2d(in_channels=channel, out_channels=channel, kernel_size=3,padding=1),
#             torch.nn.Dropout(p=dropout),
#             torch.nn.BatchNorm2d(channel)
#         )
        self.conv5_0 = torch.nn.Conv2d(in_channels=channel, out_channels=channel*extend, kernel_size=3,stride = 2,padding=1)
        self.concat4 = nn.Conv2d(in_channels=channel, out_channels=channel*extend, kernel_size=1, stride=2)
        channel=channel*extend
        
        self.conv5_1 = torch.nn.Conv2d(in_channels=channel, out_channels=channel, kernel_size=3,padding=1)
        self.conv5 = torch.nn.Sequential(
            torch.nn.BatchNorm2d(channel),
            self.act,
            torch.nn.Conv2d(in_channels=channel, out_channels=channel, kernel_size=3,padding=1),
            torch.nn.Dropout(p=dropout),
            torch.nn.BatchNorm2d(channel)
        )
        self.avgpool = nn.AvgPool2d(kernel_size=8, stride=1)
    
        self.linear1 = torch.nn.Sequential(torch.nn.Linear(in_features=channel, out_features=channel*extend_lin),
         self.act,
         torch.nn.BatchNorm1d(channel*extend_lin))                                  
        self.linear3 = torch.nn.Sequential(torch.nn.Linear(in_features=channel*extend_lin, out_features=channel),
         self.act,
         torch.nn.BatchNorm1d(channel))  
        self.output = torch.nn.Linear(in_features=channel, out_features=200)
        self.relu = self.act
        # -------------------------------------------
        #Вспомогательные параметры и функции
        # -------------------------------------------
        #self.loss_func = torch.nn.CrossEntropyLoss()
        self.targets = torch.Tensor()
        self.preds = torch.Tensor()

        
    def forward(self, x):
      #block - 0
        x = self.conv0(x)
        y = self.maxpool(x)
      # block - 1
        x = self.conv1(y)
        y= self.relu(x+y)
      #block - 2
        x = self.conv2_0(y)
        x = self.conv2(x)
        y= self.relu(self.concat1(y)+x)
      #block - 3
#         x = self.conv3_0(y)
#         x=self.conv3(x)
#         y=self.relu(self.concat2(y)+x)
#       # block - 4
#         x = self.conv4_0(y)
#         x=self.conv4(x)
#         y=self.relu(self.concat3(y)+x)
     # block - 5
        x = self.conv5_0(y)
        x=self.conv5(x)
        y=self.relu(self.concat4(y)+x)
        x = self.avgpool(y)
      # block - classifier
        x = x.view(x.size(0), -1)
        x = self.linear1(x)
        x = self.linear3(x)
        return self.output(x)
    

In [7]:
device = torch.device("cuda") if torch.cuda.is_available() else torch.device("cpu")
device

device(type='cuda')

In [8]:
epoches = 3

In [9]:
def objective(trial):
    dropout = trial.suggest_float("dropout", 1e-2, 9*1e-1)
    extend = trial.suggest_int("extend", 2, 4)
    channel = trial.suggest_int("channel", 8, 128)
    extend_lin= trial.suggest_int("extend_lin", 2, 8)
#     act = trial.suggest_categorical("act", ["ReLU", "ELU", "LeakyReLU"])
    model = YourNet(dropout =dropout,extend =extend, channel =channel,extend_lin=extend_lin, act="ELU").to(device)
#     optimizer_name = trial.suggest_categorical("optimizer", ["Adam", "RMSprop", "SGD"])
    lr = trial.suggest_float("lr", 1e-5, 1e-1, log=True)
    optimizer = getattr(optim, "Adam")(model.parameters(), lr=lr)
    loss_fun = nn.CrossEntropyLoss()
    for epoch in trange(epoches,desc = 'Эпохи обучения'):
        model.train()
        for batch_idx, (data, target) in enumerate(tqdm(train_dataloader)):
            data, target = data.to(device), target.to(device)
            optimizer.zero_grad()
            output = model(data)
            loss = loss_fun(output, target)
            loss.backward()
            optimizer.step()
        model.eval()
        correct = 0
        n = 0
        with torch.no_grad():
            for batch_idx, (data, target) in enumerate(tqdm(val_dataloader)):
                data, target = data.to(device), target.to(device)
                output = model(data)
                # Get the index of the max log-probability.
                pred = output.argmax(dim=1, keepdim=True)
                correct += pred.eq(target.view_as(pred)).sum().item()
                n += len(target)
        accuracy = correct / n
        trial.report(accuracy, epoch)

        # Handle pruning based on the intermediate value.
        if trial.should_prune():
            raise optuna.exceptions.TrialPruned()

    return accuracy

In [10]:
study = optuna.create_study(direction="maximize",
                            sampler =optuna.samplers.TPESampler(multivariate=True, group=True),
                            pruner=optuna.pruners.HyperbandPruner(min_resource=1, 
                                                                  reduction_factor=2))
study.optimize(objective, n_trials=100, timeout=4800)


C:\Users\playi\AppData\Local\Programs\Python\Python311\Lib\site-packages\optuna\samplers\_tpe\sampler.py:278: ExperimentalWarning: ``multivariate`` option is an experimental feature. The interface can change in the future.
  warnings.warn(
C:\Users\playi\AppData\Local\Programs\Python\Python311\Lib\site-packages\optuna\samplers\_tpe\sampler.py:289: ExperimentalWarning: ``group`` option is an experimental feature. The interface can change in the future.
  warnings.warn(
[I 2023-06-23 00:47:31,155] A new study created in memory with name: no-name-6c9d82db-7441-4e98-9b9c-960492021a62
  4%|███                                                                             | 59/1563 [00:10<03:08,  7.97it/s]


  8%|██████▎                                                                        | 125/1563 [00:18<03:11,  7.52it/s]


 12%|█████████▋                                                                     | 191/1563 [00:26<02:45,  8.31it/s]


 16%|████████████▉                                                                  | 257/1563 [00:34<02:38,  8.26it/s]


 21%|████████████████▎                                                              | 323/1563 [00:42<02:28,  8.34it/s]


...

 90%|██████████████████████████████████████████████████████████████████████        | 1403/1563 [02:10<00:14, 10.88it/s]


 98%|████████████████████████████████████████████████████████████████████████████▌ | 1535/1563 [02:22<00:02, 10.81it/s]


100%|██████████████████████████████████████████████████████████████████████████████| 1563/1563 [02:25<00:00, 10.76it/s]

 40%|████████████████████████████████▌                                                | 63/157 [00:06<00:11,  8.32it/s]


 82%|█████████████████████████████████████████████████████████████████▋              | 129/157 [00:15<00:03,  7.84it/s]


Эпохи обучения: 100%|███████████████████████████████████████████████████████████████████| 3/3 [08:14<00:00, 164.78s/it]
[I 2023-06-23 02:11:20,639] Trial 9 finished with value: 0.1263 and parameters: {'dropout': 0.500536765194735, 'extend': 2, 'channel': 50, 'extend_lin': 4, 'lr': 0.00022048240548645396}. Best is trial 0 with value: 0.1529.


In [11]:
pruned_trials = study.get_trials(deepcopy=False, states=[TrialState.PRUNED])
complete_trials = study.get_trials(deepcopy=False, states=[TrialState.COMPLETE])

print("Study statistics: ")
print("  Number of finished trials: ", len(study.trials))
print("  Number of pruned trials: ", len(pruned_trials))
print("  Number of complete trials: ", len(complete_trials))

print("Best trial:")
trial = study.best_trial

print("  Value: ", trial.value)

print("  Params: ")
for key, value in trial.params.items():
    print("    {}: {}".format(key, value))

Study statistics: 
  Number of finished trials:  10
  Number of pruned trials:  4
  Number of complete trials:  6
Best trial:
  Value:  0.1529
  Params: 
    dropout: 0.05667884788044004
    extend: 2
    channel: 115
    extend_lin: 2
    lr: 1.5628647366049794e-05


In [ ]:
train